In [67]:
!pip3 install pandas

Defaulting to user installation because normal site-packages is not writeable
You should consider upgrading via the '/Library/Developer/CommandLineTools/usr/bin/python3 -m pip install --upgrade pip' command.


### Get the filelist

For the full results.json

In [68]:
import glob

# Specify the path to the folder containing the results.json files
folder_path = "lm-eval-output"

# Use glob to find all the results.json files
results_json_files = glob.glob(f"{folder_path}/**/results.json", recursive=True)

# Show total number of results.json files found
print(f"Found {len(results_json_files)} results.json files")


Found 2489 results.json files


### Process all the results.json

One file at a time

In [69]:
import json

# Global result map if it's not set
if 'global_result_map' not in globals():
    global_result_map = {}

#
# Function to process the results.json file
#
def process_results_json(file_path):
    with open(file_path) as f:
        data = json.load(f)

    # Model args, presplit by ','
    model_args = data['config']['model_args'].split(',')

    # Extract the pretrained value from config.model_args
    modelname = model_args[0].split('=')[1]

    # Opt array
    confArgsArr = model_args[1:]

    # Sort the opt array
    confArgsArr.sort()
    # Convert it to a string
    confStr = ','.join(confArgsArr)

    # Convert the option array of key=value strings to a dictionary
    confObj = { }
    for o in confArgsArr:
        k, v = o.split('=')
        confObj[k] = v
    
    # Create a dictionary to store the results, or use the existing one if it exists
    if modelname in global_result_map:
        modelObj = global_result_map[modelname]
    else:
        modelObj = {
            'name': modelname,
            'config': { }
        }
    
    # Get the opt object for the model
    if confStr in modelObj['config']:
        confSet = modelObj['config'][confStr]
    else:
        confSet = {
            'confStr': confStr,
            'confObj': confObj,
            'results': {},
            'groups': {}
        }

    # Iterate over the results and extract the result object for each test/group
    if 'results' in data:
        for test, result in data['results'].items():
            confSet['results'][test] = result
    if 'groups' in data:
        for test, result in data['groups'].items():
            confSet['groups'][test] = result
    
    # Update the global result map object
    modelObj['config'][confStr] = confSet
    global_result_map[modelname] = modelObj
    return modelObj

# Lets test the function with the first results.json file
first_result = process_results_json(results_json_files[0])
print(f"Processed example: ", first_result)


Processed example:  {'name': 'mistralai/Mistral-7B-v0.1', 'config': {'dtype=bfloat16,trust_remote_code=True': {'confStr': 'dtype=bfloat16,trust_remote_code=True', 'confObj': {'dtype': 'bfloat16', 'trust_remote_code': 'True'}, 'results': {'xcopa': {'acc,none': 0.5587272727272727, 'acc_stderr,none': 0.0551636604460852, 'alias': 'xcopa'}, 'xcopa_et': {'acc,none': 0.466, 'acc_stderr,none': 0.02233126442325838, 'alias': ' - xcopa_et'}, 'xcopa_ht': {'acc,none': 0.512, 'acc_stderr,none': 0.02237662679792717, 'alias': ' - xcopa_ht'}, 'xcopa_id': {'acc,none': 0.582, 'acc_stderr,none': 0.022080014812228137, 'alias': ' - xcopa_id'}, 'xcopa_it': {'acc,none': 0.66, 'acc_stderr,none': 0.021206117013673066, 'alias': ' - xcopa_it'}, 'xcopa_qu': {'acc,none': 0.482, 'acc_stderr,none': 0.02236856511738799, 'alias': ' - xcopa_qu'}, 'xcopa_sw': {'acc,none': 0.518, 'acc_stderr,none': 0.02236856511738799, 'alias': ' - xcopa_sw'}, 'xcopa_ta': {'acc,none': 0.542, 'acc_stderr,none': 0.02230396677426995, 'alias'

In [70]:
# Lets reset and reprocess all the results.json files
global_result_map = {}

# Process all the results.json files
for file in results_json_files:
    process_results_json(file)

# Show high level list of models
print(f"Found {len(global_result_map)} models")
print(f"Models: \n{list(global_result_map.keys())}")

# Save the result map to a file
with open('summary/compiled-lm-eval-results.json', 'w') as f:
    json.dump(global_result_map, f, sort_keys=True, indent='\t')

# Echo that its been saved to json
print(f"Saved to compiled-lm-eval-results.json")

Found 38 models
Models: 
['mistralai/Mistral-7B-v0.1', 'mosaicml/mpt-7b-instruct', 'mosaicml/mpt-7b', 'mosaicml/mpt-7b-chat', 'bigscience/bloom-7b1', 'bigscience/bloomz-7b1-mt', 'bigscience/bloomz-7b1', 'EleutherAI/pythia-2.8b', 'EleutherAI/pythia-1.4b', 'EleutherAI/gpt-j-6b', 'EleutherAI/pythia-6.9b', 'google/gemma-2b', 'google/gemma-7b', 'microsoft/phi-1_5', 'microsoft/phi-2', 'microsoft/phi-1', 'allenai/OLMo-7B', 'TinyLlama/TinyLlama-1.1B-intermediate-step-1431k-3T', 'TinyLlama/TinyLlama-1.1B-Chat-v1.0', 'RWKV/rwkv-5-world-1b5', 'RWKV/rwkv-5-world-3b', 'RWKV/rwkv-4-world-3b', 'RWKV/rwkv-4-world-1b5', 'RWKV/rwkv-4-world-7b', 'RWKV/HF_v5-Eagle-7B', 'togethercomputer/RedPajama-INCITE-7B-Base', 'togethercomputer/RedPajama-INCITE-7B-Instruct', 'togethercomputer/RedPajama-INCITE-7B-Chat', 'facebook/opt-2.7b', 'facebook/opt-6.7b', 'facebook/opt-1.3b', 'tiiuae/falcon-7b-instruct', 'tiiuae/falcon-rw-1b', 'tiiuae/falcon-rw-7b', 'tiiuae/falcon-7b', 'huggyllama/llama-7b', 'meta-llama/Llama-2-7b

### Convert the results into CSV table formats

In [71]:
# Lets convert this into a table, which we will display in this notebook, and save as a CSV
import pandas as pd

##################################################
#
#  Utility functions
#
##################################################

# Check if the given name string, is within the list, including "*" wildcard
def is_in_list(name, list):
    for n in list:
        if n[-1] == '*':
            if name.startswith(n[:-1]):
                return True
        elif n == name:
            return True
    return False

# Is in inclusion exclusion list pair
def is_in_list_pair(name, inList, exList):
    if not is_in_list(name, inList):
        return False
    if is_in_list(name, exList):
        return False
    return True

# Prepare a single test/group result object
# By applying common filtering and formatting changes
def prepare_test_result(result):
    # The reutrn object
    ret = {}
    # Iterate the result key/value
    for k, v in result.items():
        # Skip if its alias
        if k == 'alias':
            continue

        # If the key ends with ",none", drop the ",none"
        if k.endswith(',none'):
            k = k[:-5]
        
        # Save the result
        ret[k] = v
    
    # Return the result
    return ret

##################################################
#
#  Generate the result
#
##################################################

# Create a list of rows for the table
def generate_result_table(
    inConfig = { "dtype": "bfloat16" },

    # Results and groups to include
    inResults = [],
    inGroups = ["*"],

    # Exclude results and groups, applied after inResults and inGroups
    exResults = [],
    exGroups = [],

    # Sorted
    sort = False
):
    table_rows = []

    # Iterate over the models
    for model, modelObj in global_result_map.items():
        # Iterate over the configurations
        for confStr, confSet in modelObj['config'].items():
            # Get the confObj
            confObj = confSet['confObj']

            # Check if the inConfig, matches the confObj
            if inConfig:
                skip = False
                for k, v in inConfig.items():
                    if k not in confObj or confObj[k] != v:
                        skip = True
                        break
                if skip:
                    continue

            # Create a row object
            row = {
                'model': model,
                # 'config': confStr

                "avg_acc": 0.0,
                "avg_acc_stderr": 0.0,
            }

            # Total acc / acc_stderr
            acc_total = 0.0
            acc_count = 0
            acc_stderr_total = 0.0
            acc_stderr_count = 0

            # Add the groups
            for test, result in confSet['groups'].items():

                # Skip if not in the inGroups or exGroups
                if not is_in_list_pair(test, inGroups, exGroups):
                    continue

                # Filter the result obj
                cleanResult = prepare_test_result(result)

                # Add the result to the row, as seperate columns for each key
                for k, v in cleanResult.items():
                    row[f"{test} ({k})"] = v

                    if k == 'acc':
                        acc_total += v
                        acc_count += 1
                    elif k == 'acc_stderr':
                        acc_stderr_total += v
                        acc_stderr_count += 1

            # Add the results
            for test, result in confSet['results'].items():

                # Skip if not in the inResults or exResults
                if not is_in_list_pair(test, inResults, exResults):
                    continue

                # Filter the result obj
                cleanResult = prepare_test_result(result)

                # Add the result to the row, as seperate columns for each key
                for k, v in cleanResult.items():
                    row[f"{test} ({k})"] = v

                    if k == 'acc':
                        acc_total += v
                        acc_count += 1
                    elif k == 'acc_stderr':
                        acc_stderr_total += v
                        acc_stderr_count += 1
                
            # Add the avg acc and acc_stderr
            if acc_count > 0:
               row["avg_acc"] = acc_total / acc_count
            if acc_stderr_count > 0:
                row["avg_acc_stderr"] = acc_stderr_total / acc_stderr_count

            # Append the row to the table
            table_rows.append(row)

    # Create a dataframe from the table rows
    df = pd.DataFrame(table_rows)

    # Sort by avg_acc
    if sort:
        df = df.sort_values(by='avg_acc', ascending=False)

    # Show the dataframe
    return df

# Generate the dataframe
df = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["xcopa"], inResults=[] )

# # Save the dataframe to a CSV file
# df.to_csv('summary/compiled-lm-eval-results.csv', index=False)

# Show results
df


model   avg_acc  \
0                           mistralai/Mistral-7B-v0.1  0.558727   
1                            mosaicml/mpt-7b-instruct  0.537091   
2                                     mosaicml/mpt-7b  0.536000   
3                                mosaicml/mpt-7b-chat  0.538000   
4                                bigscience/bloom-7b1  0.570909   
5                            bigscience/bloomz-7b1-mt  0.546000   
6                               bigscience/bloomz-7b1  0.547818   
7                              EleutherAI/pythia-2.8b  0.537455   
8                              EleutherAI/pythia-1.4b  0.526545   
9                                 EleutherAI/gpt-j-6b  0.544182   
10                             EleutherAI/pythia-6.9b  0.540545   
11                                    google/gemma-2b  0.520545   
12                                    google/gemma-7b  0.517636   
13                                  microsoft/phi-1_5  0.521636   
14                                    microsoft/phi-2  0.512182   
15                                    microsoft/phi-1  0.517636   
16                                    allenai/OLMo-7B  0.537818   
17  TinyLlama/TinyLlama-1.1B-intermediate-step-143...  0.529273   
18                 TinyLlama/TinyLlama-1.1B-Chat-v1.0  0.528909   
19                              RWKV/rwkv-5-world-1b5  0.578909   
20                               RWKV/rwkv-5-world-3b  0.590182   
21                               RWKV/rwkv-4-world-3b  0.575455   
22                              RWKV/rwkv-4-world-1b5  0.554000   
23                               RWKV/rwkv-4-world-7b  0.601455   
24                                RWKV/HF_v5-Eagle-7B  0.621818   
25          togethercomputer/RedPajama-INCITE-7B-Base  0.525455   
26      togethercomputer/RedPajama-INCITE-7B-Instruct  0.528545   
27          togethercomputer/RedPajama-INCITE-7B-Chat  0.535455   
28                                  facebook/opt-2.7b  0.521818   
29                                  facebook/opt-6.7b  0.522909   
30                                  facebook/opt-1.3b  0.521818   
31                          tiiuae/falcon-7b-instruct  0.536727   
32                                tiiuae/falcon-rw-1b  0.522545   
33                                tiiuae/falcon-rw-7b  0.535818   
34                                   tiiuae/falcon-7b  0.559636   
35                                huggyllama/llama-7b  0.541818   
36                      meta-llama/Llama-2-7b-chat-hf  0.000000   
37                           meta-llama/Llama-2-7b-hf  0.566727   

    avg_acc_stderr  xcopa (acc)  xcopa (acc_stderr)  
0         0.055164     0.558727            0.055164  
1         0.041919     0.537091            0.041919  
2         0.042339     0.536000            0.042339  
3         0.047059     0.538000            0.047059  
4         0.061359     0.570909            0.061359  
5         0.038321     0.546000            0.038321  
6         0.038920     0.547818            0.038920  
7         0.026941     0.537455            0.026941  
8         0.027441     0.526545            0.027441  
9         0.034404     0.544182            0.034404  
10        0.029689     0.540545            0.029689  
11        0.025332     0.520545            0.025332  
12        0.027330     0.517636            0.027330  
13        0.026198     0.521636            0.026198  
14        0.029742     0.512182            0.029742  
15        0.029612     0.517636            0.029612  
16        0.034147     0.537818            0.034147  
17        0.029316     0.529273            0.029316  
18        0.031702     0.528909            0.031702  
19        0.045103     0.578909            0.045103  
20        0.056241     0.590182            0.056241  
21        0.040977     0.575455            0.040977  
22        0.039406     0.554000            0.039406  
23        0.053116     0.601455            0.053116  
24        0.068986     0.621818            0.068986  
25        0.036407     0.52545

In [72]:
##################################################
#
#  Build the various subsets
#
##################################################

# Overall results
all_results = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"] )
all_results.to_csv('summary/bf16-all-results-and-groups.csv', index=False)

# Multilang results
multiLang_tTest = ["xcopa_*", "xnli_*", "xstorycloze_*", "xwinograd_*", "lambada_openai_*",     "pawsx_*"]
multiLang_tGrps = ["xcopa",   "xnli",   "xstorycloze",   "xwinograd",   "lambada_multilingual", "pawsx"]

multilang_grp = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[] )
multilang_test = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=multiLang_tTest )
multilang_grp.to_csv('summary/bf16-multilang-summary.csv', index=False)
multilang_test.to_csv('summary/bf16-multilang-results.csv', index=False)

multilang_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=multiLang_tGrps, inResults=[], sort=True )
multilang_grp_sorted.to_csv('summary/bf16-sorted-multilang-summary.csv', index=False)

# All other results
eng_grp = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=[], exGroups=multiLang_tGrps )
eng_grp_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=[], exGroups=multiLang_tGrps, sort=True )
eng_test = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], exGroups=multiLang_tGrps, exResults=multiLang_tTest )
eng_test_sorted = generate_result_table( inConfig = { "dtype": "bfloat16" }, inGroups=["*"], inResults=["*"], exGroups=multiLang_tGrps, exResults=multiLang_tTest, sort=True )

eng_grp.to_csv('summary/bf16-eng-summary.csv', index=False)
eng_test.to_csv('summary/bf16-eng-results.csv', index=False)
eng_test_sorted.to_csv('summary/bf16-sorted-eng-results.csv', index=False)
eng_grp_sorted.to_csv('summary/bf16-sorted-eng-summary.csv', index=False)

# List the files
!ls -lh summary

total 14648
-rw-r--r--@ 1 picocreator  staff   928K Feb 22 16:11 bf16-all-results-and-groups.csv
-rw-r--r--@ 1 picocreator  staff   853K Feb 22 16:11 bf16-eng-results.csv
-rw-r--r--@ 1 picocreator  staff    72K Feb 22 16:11 bf16-eng-summary.csv
-rw-r--r--@ 1 picocreator  staff    88K Feb 22 16:11 bf16-multilang-results.csv
-rw-r--r--@ 1 picocreator  staff    12K Feb 22 16:11 bf16-multilang-summary.csv
-rw-r--r--@ 1 picocreator  staff   853K Feb 22 16:11 bf16-sorted-eng-results.csv
-rw-r--r--@ 1 picocreator  staff    72K Feb 22 16:11 bf16-sorted-eng-summary.csv
-rw-r--r--@ 1 picocreator  staff    12K Feb 22 16:11 bf16-sorted-multilang-summary.csv
-rw-r--r--  1 picocreator  staff   3.6M Feb 22 16:11 compiled-lm-eval-results.json
